In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px

In [2]:

df= pd.read_csv('../data/analysis/biomarker_measurement.csv')

df["measurement_datetime"] = pd.to_datetime(
    df["measurement_datetime"],
    format="mixed",
    errors="coerce"
)

df["procedure_datetime"] = pd.to_datetime(
    df["procedure_datetime"],
    format="mixed",
    errors="coerce"
)

In [3]:
df["day_from_procedure"] = (
    df["measurement_datetime"].dt.normalize()
    - df["procedure_datetime"].dt.normalize()
).dt.days

In [4]:
df = df.rename(columns={"value_as_number": "biomarker_value"})

In [5]:
BIOMARKER_CONCEPT_ID = 3034426

df = df[df["measurement_concept_id"] == BIOMARKER_CONCEPT_ID]

In [6]:
# ------------------------------------------------
# 3) LOS → color mapping
# ------------------------------------------------
los_min = df["los_days"].min()
los_max = df["los_days"].max()

colorscale = px.colors.sequential.Blues

def los_to_color(los):
    if los_max == los_min:
        t = 0.5
    else:
        t = (los - los_min) / (los_max - los_min)
    return px.colors.sample_colorscale(colorscale, t)[0]


In [7]:
fig = go.Figure()
for person_id, g in (
    df.sort_values("day_from_procedure")
      .groupby("person_id")
):
    los = float(g["los_days"].iloc[0])
    color = los_to_color(los)

    fig.add_trace(
        go.Scatter(
            x=g["day_from_procedure"],
            y=g["biomarker_value"],
            mode="lines+markers",
            line=dict(color=color, width=2),
            marker=dict(size=5, color=color),
            customdata=np.column_stack([
                np.repeat(person_id, len(g)),
                np.repeat(los, len(g))
            ]),
            hovertemplate=(
                "Patient: %{customdata[0]}<br>"
                "LOS: %{customdata[1]} days<br>"
                "Day: %{x}<br>"
                "Value: %{y}<extra></extra>"
            ),
            showlegend=False
        )
    )

    fig.add_vline(
    x=0,
    line_width=2,
    line_dash="dash",
    line_color="red",
    annotation_text="Procedure day",
    annotation_position="top"
)

In [8]:
range_low = df["range_low"].dropna().unique()
range_high = df["range_high"].dropna().unique()

In [9]:
if len(range_low) == 1 and len(range_high) == 1:
    fig.add_hrect(
        y0=range_low[0],
        y1=range_high[0],
        fillcolor="green",
        opacity=0.12,
        line_width=0,
        annotation_text="Normal range",
        annotation_position="top left"
    )

In [10]:
fig.add_trace(
    go.Scatter(
        x=[None], y=[None],
        mode="markers",
        marker=dict(
            colorscale=colorscale,
            cmin=los_min,
            cmax=los_max,
            color=[los_min, los_max],
            showscale=True,
            colorbar=dict(
                title="Length of Stay (days)",
                len=0.85
            ),
            size=10,
            opacity=0
        ),
        hoverinfo="skip",
        showlegend=False
    )
)

In [11]:
fig.update_layout(
    title="Creatinine trajectories around procedure (colored by LOS)",
    xaxis_title="Days from procedure (t = 0)",
    yaxis_title="Creatinine",
    template="simple_white",
    width=1150,
    height=550
)


In [12]:
fig.show()